# Image Detection on a BigDL Cluster

Image detection. please refer to the BigDL sample in below link
https://github.com/intel-analytics/BigDL/tree/master/spark/dl/src/main/scala/com/intel/analytics/bigdl/example/imageclassification

## Intialization

* import necesary libraries

In [52]:
import os
from PIL import Image, ImageDraw, ImageFont
from IPython.display import Image, display
%pylab inline
from moviepy.editor import *

Populating the interactive namespace from numpy and matplotlib


## function that generates a video clip from images 

* input a folder with images, and generated a video clip with assigned FPS

In [53]:
def video_playback_from_images(filepath,Duration):
    base_dir = os.path.realpath(filepath)
    directory=sorted(os.listdir(filepath))[:30]
    clips=[]
    for filename in directory:
        if filename.endswith(".JPEG"):
            readfile= filepath+'/'+filename
            clips.append(ImageClip(readfile).set_duration(Duration))

    video = concatenate(clips, method="compose")
    return video
    #video.ipython_display(fps=120, loop=True, autoplay=True)

filepath='/home/ubuntu/install_files/ILSVRC2012_img_val/1000_images'
Duration=0.5
Fps = 120
video1 = video_playback_from_images(filepath,Duration)
video1.ipython_display(fps=Fps, loop=True, autoplay=True)

t:   1%|▏         | 25/1800 [00:00<00:07, 243.54it/s, now=None]

Moviepy - Building video __temp__.mp4.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4


## Function that puts the detection results into images and generates a video clip accordingly

* put the detection result on the image and generated a video clip for those images with detection result

In [54]:
def generated_infer_images_and_playback_in_video(result_file,outfolder,pics_in_video):
    pic_index=0
    #default fps and duration
    Fps=0
    Duration=0
    if os.path.isdir(outfolder) == False:
        os.mkdir(outfolder)

    with open(result_file) as f:
        lines = f.readlines()
    for line in lines:
            if line.find('sec')!=-1:
                elapsed_sec = line.split(' ')[2]
                #print elapsed_sec
                Duration = float(elapsed_sec)/1000.0
                Fps= 1000.0/float(elapsed_sec)
                print Duration , Fps
    for line in lines:
            if line.find('ILSVRC2012_val_0')!=-1:
                line = line.strip('\n')
                line = line.strip('[')
                line = line.strip(']')
                filename = line.split(',')[0]
                idnum = line.split(',')[1]
            
                pic_index+=1
                if pic_index >= pics_in_video:
                    break
                #print filename,idnum
                if filename.endswith(".JPEG"):
                    readfile= filepath+'/'+filename
                    writefile=outfolder+'/'+filename
                    if os.path.isfile(readfile):
                        #print readfile
                        # overlay image with idnum
                        from PIL import Image, ImageDraw, ImageFont
                        img = Image.open(readfile)
                        draw = ImageDraw.Draw(img)
                        font = ImageFont.truetype(r'./Serif.ttf', 100)
                        draw.text((0, 0),idnum,(0,0,0),font=font)
                        img.save(writefile)
                        
    video = video_playback_from_images(outfolder,Duration)  
    
    return video, Fps
 

## Initialize BigDL environment variables

In [55]:
!~/env.sh
!echo $BIGDL_HOME

/home/ubuntu/BigDL/dist


## BigDL local mode with single Spark worker node

* Submit the BigDL image detection work into Apach Spark cluster and use local mode in this case

In [56]:
!spark-submit --master local[1] \
--driver-memory 16g \
--executor-memory 16g  \
--class com.intel.analytics.bigdl.example.imageclassification.ImagePredictor \
$BIGDL_HOME/lib/bigdl-0.9.0-SNAPSHOT-jar-with-dependencies.jar \
--modelPath /home/ubuntu/install_files/trained_models/resnet-18.t7 \
--folder /home/ubuntu/install_files/ILSVRC2012_img_val/1000_images \
--modelType torch --batchSizePerCore 16  \
--isHdfs false \
--showNum 1000 \
 2>&1 | tee ./single_node.txt




19/06/21 00:24:55 INFO utils.Engine$: Auto detect executor number and executor cores number
19/06/21 00:24:55 INFO utils.Engine$: Executor number is 1 and executor cores number is 1
19/06/21 00:24:56 INFO utils.ThreadPool$: Set mkl threads to 1 on thread 1
19/06/21 00:24:56 INFO utils.Engine$: Find existing spark context. Checking the spark conf...
Start to read directories /home/ubuntu/install_files/ILSVRC2012_img_val/1000_images
^C


## visualize detection back to clips

In [51]:
result_file='./single_node.txt'
outfolder = './single_node'
pics_in_video=30
video2, Fps = generated_infer_images_and_playback_in_video(result_file,outfolder,pics_in_video)
print Fps
video2.ipython_display(fps=Fps, loop=True, autoplay=True)

0.112 8.92857142857


8.92857142857
Moviepy - Building video __temp__.mp4.
Moviepy - Writing video __temp__.mp4

Moviepy - Done !
Moviepy - video ready __temp__.mp4


## BigDL standalone mode with mulitple Spark worker nodes

* Submit the BigDL image detection work into Apach Spark cluster and use standalone mode with 8 workder nodes in this case

In [32]:
!spark-submit --master spark://ec2-18-224-14-193.us-east-2.compute.amazonaws.com:7077  \
--executor-cores 1  \
--total-executor-cores 8 \
--driver-memory 16g \
--executor-memory 16g \
--conf spark.network.timeout=10000000 \
--class com.intel.analytics.bigdl.example.imageclassification.ImagePredictor \
$BIGDL_HOME/lib/bigdl-0.9.0-SNAPSHOT-jar-with-dependencies.jar \
--modelPath /home/ubuntu/install_files/trained_models/resnet-18.t7 \
--folder /home/ubuntu/install_files/ILSVRC2012_img_val/1000_images \
--modelType torch --batchSizePerCore 16  \
--isHdfs false \
--showNum 1000 \
 2>&1 | tee ./multi_node.txt

^C


## visualize detection back to clips

In [48]:
result_file='./multi_node.txt'
outfolder = './multi_node'
pics_in_video=30
pics_for_inference = 1000
video3, Fps = generated_infer_images_and_playback_in_video(result_file,outfolder,pics_in_video,pics_for_inference)
video3.ipython_display(fps=Fps, loop=True, autoplay=True)

0.02 50.0


Moviepy - Building video __temp__.mp4.
Moviepy - Writing video __temp__.mp4

Moviepy - Done !
Moviepy - video ready __temp__.mp4
